# ragas

## Ensemble

In [1]:
# ==============================================================
# 0️⃣ 라이브러리 불러오기
# ==============================================================
import os
import json
import pandas as pd
from dotenv import load_dotenv
from datasets import Dataset
from ragas import evaluate
from ragas.metrics import (
    context_precision,
    faithfulness,
    answer_relevancy,
    context_recall,
)

# ==============================================================
# 1️⃣ API KEY 로드
# ==============================================================
load_dotenv()  # .env 파일에서 환경변수 로드

# ==============================================================
# 2️⃣ Ground truth JSON 파일 로드 및 매핑
# ==============================================================
json_paths = [
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_016_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_022_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_035_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_039_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_040_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_041_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_042_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_044_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_056_gt.json",
]

rel_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/context_per_model/relevance_cat3_context_df.csv"
)
rel = pd.read_csv(rel_path)

# ground_truth 딕셔너리 생성
gt_dict = {}
for path in json_paths:
    paper_num = path.split("/")[-1].split("_")[1]  # 파일명에서 paper_num 추출
    with open(path, "r", encoding="utf-8") as f:
        data = json.load(f)
    gt_dict[paper_num] = data["Morphological Properties"]

# paper_num을 3자리 문자열로 변환하여 매핑
rel["paper_num_str"] = rel["paper_num"].apply(lambda x: f"{x:03d}")
rel["ground_truth"] = rel["paper_num_str"].map(gt_dict)
rel["ground_truth"] = rel["ground_truth"].apply(
    lambda x: x if isinstance(x, dict) else {}
)

# ==============================================================
# 3️⃣ Context 통합
# ==============================================================
context_cols = [f"context_{i}" for i in range(9)]
rel["context"] = rel[context_cols].values.tolist()  # 리스트 형태로 합치기

rel.drop("paper_num_str", axis=1, inplace=True)

# ==============================================================
# 4️⃣ Question 정의
# ==============================================================
question_template =     """  question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}
        
        """

rel["question_list"] = [question_template] * len(rel)

# ==============================================================
# 5️⃣ 문자열 변환: RAGAS에서 Arrow 호환되도록
# ==============================================================
rel["answer_str"] = rel["json_answer"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)
rel["ground_truth_str"] = rel["ground_truth"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)

# ==============================================================
# 6️⃣ 열 이름 통일 및 Dataset 생성
# ==============================================================
rel["question"] = rel["question_list"]  # 문자열
rel["answer"] = rel["answer_str"]  # 문자열
rel["ground_truth"] = rel["ground_truth_str"]  # 문자열
rel["contexts"] = rel["context"].apply(
    lambda lst: [str(x) if x is not None else "" for x in lst]
)  # 리스트 그대로


# Dataset1
rel1 = rel.iloc[0:10, :]

ragas_dataset1 = Dataset.from_pandas(
    rel1[["question", "answer", "ground_truth", "contexts"]]
)
# Dataset2 생성
ragas_dataset100 = Dataset.from_pandas(
    rel[["question", "answer", "ground_truth", "contexts"]]
)

/Users/limseongbeom/anaconda3/envs/voltai/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:
import json
from decimal import Decimal

try:
    import numpy as np
except Exception:
    np = None

def make_json_serializable(obj):
    # 기본 타입
    if obj is None or isinstance(obj, (str, bool, int, float)):
        return obj
    # Decimal -> float
    if isinstance(obj, Decimal):
        return float(obj)
    # numpy types
    if np is not None:
        if isinstance(obj, np.generic):
            return obj.item()
        if isinstance(obj, np.ndarray):
            return obj.tolist()
    # dict -> 재귀 처리
    if isinstance(obj, dict):
        return {str(k): make_json_serializable(v) for k, v in obj.items()}
    # list/tuple/set -> 재귀 처리
    if isinstance(obj, (list, tuple, set)):
        return [make_json_serializable(v) for v in obj]
    # pydantic/BaseModel-like 객체 처리 (dict() 사용)
    if hasattr(obj, "dict") and callable(getattr(obj, "dict")):
        try:
            return make_json_serializable(obj.dict())
        except Exception:
            pass
    # to_dict() 사용 가능하면 사용
    if hasattr(obj, "to_dict") and callable(getattr(obj, "to_dict")):
        try:
            return make_json_serializable(obj.to_dict())
        except Exception:
            pass
    # dataclass 처리
    try:
        from dataclasses import is_dataclass, asdict
        if is_dataclass(obj):
            return make_json_serializable(asdict(obj))
    except Exception:
        pass
    # __dict__ 로 변환 시도
    if hasattr(obj, "__dict__"):
        try:
            return make_json_serializable(vars(obj))
        except Exception:
            pass
    # 마지막 수단: 문자열로 변환 (구조 손실 가능)
    return str(obj)


In [10]:
# ==============================================================
# 7️⃣ RAGAS 평가 실행
# ==============================================================

all_results = []

for i in range(1, 101):  # 100번 반복
    result = evaluate(
        dataset=ragas_dataset1,
        metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
        column_map={
            "user_input": "question",
            "ai_output": "answer",
            "reference": "ground_truth",
            "retrieved_contexts": "contexts",
            "response": "answer",
        },
    )

    # dict 변환 시도
    if hasattr(result, "to_dict"):
        result_dict = result.to_dict()
    elif hasattr(result, "dict"):
        result_dict = result.dict()
    else:
        # 필요 시 재귀 변환 함수 사용
        result_dict = make_json_serializable(result)

    # 실행 번호(run) 추가
    result_dict["run"] = i

    all_results.append(result_dict)

# DataFrame 변환
df = pd.DataFrame(all_results)

# CSV로 저장
df.to_csv("ragas_eval_rel_results.csv", index=False, encoding="utf-8-sig")

print("✅ 저장 완료: ragas_eval_rel_results.csv")

# result100 = evaluate(
#     dataset=ragas_dataset100,
#     metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
#     column_map={
#         "user_input": "question",
#         "ai_output": "answer",
#         "reference": "ground_truth",
#         "retrieved_contexts": "contexts",
#         "response": "answer",
#     },
# )

# print(result100)

Evaluating: 100%|██████████| 40/40 [01:01<00:00,  1.55s/it]
/var/folders/nz/glbk0zl17d35x39jy85r5vhc0000gn/T/ipykernel_5392/627761229.py:31: PydanticDeprecatedSince20: The `dict` method is deprecated; use `model_dump` instead. Deprecated in Pydantic V2.0 to be removed in V3.0. See Pydantic V2 Migration Guide at https://errors.pydantic.dev/2.10/migration/
  return make_json_serializable(obj.dict())
Evaluating: 100%|██████████| 40/40 [01:07<00:00,  1.69s/it]
/var/folders/nz/glbk0zl17d35x39jy85r5vhc0000gn/T/ipykernel_5392/627761229.py:31: PydanticDeprecatedSince20: The `dict` method is deprecated; use `model_dump` instead. Deprecated in Pydantic V2.0 to be removed in V3.0. See Pydantic V2 Migration Guide at https://errors.pydantic.dev/2.10/migration/
  return make_json_serializable(obj.dict())
Evaluating: 100%|██████████| 40/40 [01:36<00:00,  2.40s/it]
/var/folders/nz/glbk0zl17d35x39jy85r5vhc0000gn/T/ipykernel_5392/627761229.py:31: PydanticDeprecatedSince20: The `dict` method is deprecate

✅ 저장 완료: ragas_eval_rel_results.csv


## Relevance

In [3]:
# ==============================================================
# 0️⃣ 라이브러리 불러오기
# ==============================================================
import os
import json
import pandas as pd
from dotenv import load_dotenv
from datasets import Dataset
from ragas import evaluate
from ragas.metrics import (
    context_precision,
    faithfulness,
    answer_relevancy,
    context_recall,
)

# ==============================================================
# 1️⃣ API KEY 로드
# ==============================================================
load_dotenv()  # .env 파일에서 환경변수 로드

# ==============================================================
# 2️⃣ Ground truth JSON 파일 로드 및 매핑
# ==============================================================
json_paths = [
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_016_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_022_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_035_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_039_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_040_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_041_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_042_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_044_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_056_gt.json",
]

rel_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/context_per_model/relevance_cat3_context_df.csv"
)
rel = pd.read_csv(rel_path)

# ground_truth 딕셔너리 생성
gt_dict = {}
for path in json_paths:
    paper_num = path.split("/")[-1].split("_")[1]  # 파일명에서 paper_num 추출
    with open(path, "r", encoding="utf-8") as f:
        data = json.load(f)
    gt_dict[paper_num] = data["Morphological Properties"]

# paper_num을 3자리 문자열로 변환하여 매핑
rel["paper_num_str"] = rel["paper_num"].apply(lambda x: f"{x:03d}")
rel["ground_truth"] = rel["paper_num_str"].map(gt_dict)
rel["ground_truth"] = rel["ground_truth"].apply(
    lambda x: x if isinstance(x, dict) else {}
)

# ==============================================================
# 3️⃣ Context 통합
# ==============================================================
context_cols = [f"context_{i}" for i in range(9)]
rel["context"] = rel[context_cols].values.tolist()  # 리스트 형태로 합치기

rel.drop("paper_num_str", axis=1, inplace=True)

# ==============================================================
# 4️⃣ Question 정의
# ==============================================================
question_template =     """question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}
"""

rel["question_list"] = [question_template] * len(rel)

# ==============================================================
# 5️⃣ 문자열 변환: RAGAS에서 Arrow 호환되도록
# ==============================================================
rel["answer_str"] = rel["json_answer"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)
rel["ground_truth_str"] = rel["ground_truth"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)

# ==============================================================
# 6️⃣ 열 이름 통일 및 Dataset 생성
# ==============================================================
rel["question"] = rel["question_list"]  # 문자열
rel["answer"] = rel["answer_str"]  # 문자열
rel["ground_truth"] = rel["ground_truth_str"]  # 문자열
rel["contexts"] = rel["context"].apply(
    lambda lst: [str(x) if x is not None else "" for x in lst]
)  # 리스트 그대로


# Dataset1
rel1 = rel.iloc[0:10, :]

ragas_dataset1 = Dataset.from_pandas(
    rel1[["question", "answer", "ground_truth", "contexts"]]
)
# Dataset2 생성
ragas_dataset100 = Dataset.from_pandas(
    rel[["question", "answer", "ground_truth", "contexts"]]
)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [ ]:
# ==============================================================
# 7️⃣ RAGAS 평가 실행
# ==============================================================
result1 = evaluate(
    dataset=ragas_dataset1,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result1)

result100 = evaluate(
    dataset=ragas_dataset100,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result100)

Evaluating: 100%|██████████| 40/40 [00:59<00:00,  1.48s/it]


{'context_precision': 0.9014, 'faithfulness': 0.6378, 'answer_relevancy': 0.7145, 'context_recall': 0.6833}


Evaluating: 100%|██████████| 400/400 [06:41<00:00,  1.00s/it]


{'context_precision': 0.8730, 'faithfulness': 0.5853, 'answer_relevancy': 0.7345, 'context_recall': 0.5674}


## multi agent


In [10]:


# ==============================================================
# 0️⃣ 라이브러리 불러오기
# ==============================================================
import os
import json
import pandas as pd
from dotenv import load_dotenv
from datasets import Dataset
from ragas import evaluate
from ragas.metrics import (
    context_precision,
    faithfulness,
    answer_relevancy,
    context_recall,
    answer_correctness,
    
)

# ==============================================================
# 1️⃣ API KEY 로드
# ==============================================================
load_dotenv()  # .env 파일에서 환경변수 로드

# ==============================================================
# 2️⃣ Ground truth JSON 파일 로드 및 매핑
# ==============================================================
json_paths = [
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_016_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_022_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_035_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_039_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_040_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_041_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_042_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_044_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_056_gt.json",
]

mul_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/context_per_model/multiagent_cat3_context_df.csv"
)
mul = pd.read_csv(mul_path)

# ground_truth 딕셔너리 생성
gt_dict = {}
for path in json_paths:
    paper_num = path.split("/")[-1].split("_")[1]  # 파일명에서 paper_num 추출
    with open(path, "r", encoding="utf-8") as f:
        data = json.load(f)
    gt_dict[paper_num] = data["Morphological Properties"]

# paper_num을 3자리 문자열로 변환하여 매핑
mul["paper_num_str"] = mul["paper_num"].apply(lambda x: f"{x:03d}")
mul["ground_truth"] = mul["paper_num_str"].map(gt_dict)
mul["ground_truth"] = mul["ground_truth"].apply(
    lambda x: x if isinstance(x, dict) else {}
)

# ==============================================================
# 3️⃣ Context 통합
# ==============================================================
context_cols = [f"context_{i}" for i in range(9)]
mul["context"] = mul[context_cols].values.tolist()  # 리스트 형태로 합치기

mul.drop("paper_num_str", axis=1, inplace=True)

# ==============================================================
# 4️⃣ Question 정의
# ==============================================================
question_template =     """ 
question_text: |
    Please fill out the following JSON structure by referring to the PDF. Verify accurate values for each field. If the information is not mentioned in the PDF, write `null` (not `None`).
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}"""

mul["question_list"] = [question_template] * len(mul)

# ==============================================================
# 5️⃣ 문자열 변환: RAGAS에서 Arrow 호환되도록
# ==============================================================
mul["answer_str"] = mul["json_answer"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)
mul["ground_truth_str"] = mul["ground_truth"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)

# ==============================================================
# 6️⃣ 열 이름 통일 및 Dataset 생성
# ==============================================================
mul["question"] = mul["question_list"]  # 문자열
mul["answer"] = mul["answer_str"]  # 문자열
mul["ground_truth"] = mul["ground_truth_str"]  # 문자열
mul["contexts"] = mul["context"].apply(
    lambda lst: [str(x) if x is not None else "" for x in lst]
)  # 리스트 그대로


# Dataset1
mul1 = mul.iloc[50:60, :]

ragas_dataset1 = Dataset.from_pandas(
    mul1[["question", "answer", "ground_truth", "contexts"]]
)
# Dataset2 생성
ragas_dataset100 = Dataset.from_pandas(
    mul[["question", "answer", "ground_truth", "contexts"]]
)

In [8]:
print("/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json")

/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json


In [ ]:
mul

paper_num                                        json_answer  \
0          11  {'Morphological Properties': {'Particle size':...   
1          16  {'Morphological Properties': {'ParticleSize': ...   
2          22  {'Morphological Properties': {'Particle size':...   
3          35  {'Morphological Properties': {'ParticleSize': ...   
4          39  {'Morphological Properties': {'ParticleSize': ...   
..        ...                                                ...   
95         40  {'Morphological Properties': {'ParticleSize': ...   
96         41  {'Morphological Properties': {'Particle size':...   
97         42  {'Morphological Properties': {'ParticleSize': ...   
98         44  {'Morphological Properties': {'Particle size':...   
99         56  {'Morphological Properties': {'ParticleSize': ...   

                                            context_0  \
0   6\n\nA. Habibi et al. / Journal of Alloys and ...   
1   Figure 2 shows the SEM and TEM images of NCM a...   
2   Results and Discussion\nThe XRD patterns of pr...   
3   4. Conclusions\n\nand\n\ncurrent\n\n(GITT),\n\...   
4   2205122  (3 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
..                                                ...   
95  each\n\nonly\n\ncase\n\nand\n\nthe\n\nthe\n\nI...   
96  The SEM images for the pristine NCM-811, g-C3N...   
97  3. Results and discussion\n\nFig. 2 shows the ...   
98  Electrode Preparation and Battery Assembly. Th...   
99  For confirming the microstructural information...   

                                            context_1  \
0   Different fractions of RGO (1, 3 and 5 wt %) w...   
1   was conducted on the electrochemical equipment...   
2   experimental section\nFor  the  synthesis  of ...   
3   The studies of the LiNi0.85Co0.10Mn0.05O2 elec...   
4   3. Conclusions\n\nHerein, it is unequivocally ...   
..                                                ...   
95  3.3% may be close to the optimum value achieva...   
96  ACS Omega\n\nhttp://pubs.acs.org/journal/acsod...   
97  In order to cope with the above problems, scho...   
98  ACS Omega\n\nArticle\n\npolymer/γ-Al2O3-coated...   
99  15247\n\nF I G U R E 2\nimage on the cross-sec...   

                                            context_2  \
0   The electrochemical performances of the as-pre...   
1   ACS Applied Materials & Interfaces\n\nResearch...   
2   XPS analysis was performed to gain further inf...   
3   A.V. Ivanishchev et al.\n\nJournal of Electroa...   
4   investigated  using  XRD  analysis,  and \n\nB...   
..                                                ...   
95  juergen.janek@phys.chemie.\n\nIncreasing the N...   
96  via centrifugation at a speed of 5000 rpm for ...   
97  NJC\n\nPAPER\n\nCite this: New J. Chem., 2021,...   
98  site\n\n3a\n\n3b\n\n6c\n\nx\n\n0\n0\n0\n0\n0\n...   
99  DLiþ 1⁄4 R2T2=2n4F4A2σ2c2\n\nZ0 1⁄4 Rct þ Re þ...   

                                            context_3  \
0   As mentioned above, the RGO was added to the N...   
1   The Nyquist plots are fitted and presented in ...   
2   4\n\nwww.nature.com/scientificreportswww.natur...   
3   A.V. Ivanishchev et al.\n\nJournal of Electroa...   
4   2205122  (2 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
..                                                ...   
95  Journal of The Electrochemical Society, 2022 1...   
96  for\n\nThe electrochemical performance is furt...   
97  2.3 Electrochemical measurement\n\nCR2032 butt...   
98  Figure 1a. NCM622 particles were first soaked ...   
99  3\n\n| R E S U L T A N D DI S C U S S I O N\n\...   

                                            context_4  \
0   (cid:3)12 cm2 s\n\n4. Conclusion\n\nSolution c...   
1   Table 4. EIS Parameters of NCM and NCM/C after...   
2   V-0.02\n\nRSEI(Ω)\n\n35.838\n\n20.826\n\n26.66...   
3   Journal of Electroanalytical Chemistry 932 (20...   
4   Small 2023, 19, 2205122\n\n2205122  (6 of 13)\...   
..                                                ...   
95  Supplementary material for this article is a

In [ ]:
# ==============================================================
# 7️⃣ RAGAS 평가 실행
# ==============================================================
result1 = evaluate(
    dataset=ragas_dataset1,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall,answer_correctness],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result1)

result100 = evaluate(
    dataset=ragas_dataset100,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result100)

Evaluating: 100%|██████████| 50/50 [01:08<00:00,  1.38s/it]


{'context_precision': 0.7514, 'faithfulness': 0.7278, 'answer_relevancy': 0.7542, 'context_recall': 0.7067, 'answer_correctness': 0.6427}


Evaluating: 100%|██████████| 400/400 [06:32<00:00,  1.02it/s]


{'context_precision': 0.7675, 'faithfulness': 0.6545, 'answer_relevancy': 0.7388, 'context_recall': 0.7082}


In [ ]:
# ==============================================================
# 0️⃣ 라이브러리 불러오기
# ==============================================================
import os
import json
import pandas as pd
from dotenv import load_dotenv
from datasets import Dataset
from ragas import evaluate
from ragas.metrics import (
    context_precision,
    faithfulness,
    answer_relevancy,
    context_recall,
)

# ==============================================================
# 1️⃣ API KEY 로드
# ==============================================================
load_dotenv()  # .env 파일에서 환경변수 로드

# ==============================================================
# 2️⃣ Ground truth JSON 파일 로드 및 매핑
# ==============================================================
json_paths = [
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_016_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_022_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_035_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_039_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_040_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_041_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_042_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_044_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_056_gt.json",
]

ens_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/multiagent_cat3_context_df.csv"
)
ens = pd.read_csv(ens_path)

# ground_truth 딕셔너리 생성
gt_dict = {}
for path in json_paths:
    paper_num = path.split("/")[-1].split("_")[1]  # 파일명에서 paper_num 추출
    with open(path, "r", encoding="utf-8") as f:
        data = json.load(f)
    gt_dict[paper_num] = data["Morphological Properties"]

# paper_num을 3자리 문자열로 변환하여 매핑
ens["paper_num_str"] = ens["paper_num"].apply(lambda x: f"{x:03d}")
ens["ground_truth"] = ens["paper_num_str"].map(gt_dict)
ens["ground_truth"] = ens["ground_truth"].apply(
    lambda x: x if isinstance(x, dict) else {}
)

# ==============================================================
# 3️⃣ Context 통합
# ==============================================================
context_cols = [f"context_{i}" for i in range(9)]
ens["context"] = ens[context_cols].values.tolist()  # 리스트 형태로 합치기

ens.drop("paper_num_str", axis=1, inplace=True)

# ==============================================================
# 4️⃣ Question 정의
# ==============================================================
question_template =     """  question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}
        
        """

ens["question_list"] = [question_template] * len(ens)

# ==============================================================
# 5️⃣ 문자열 변환: RAGAS에서 Arrow 호환되도록
# ==============================================================
ens["answer_str"] = ens["json_answer"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)
ens["ground_truth_str"] = ens["ground_truth"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)

# ==============================================================
# 6️⃣ 열 이름 통일 및 Dataset 생성
# ==============================================================
ens["question"] = ens["question_list"]  # 문자열
ens["answer"] = ens["answer_str"]  # 문자열
ens["ground_truth"] = ens["ground_truth_str"]  # 문자열
ens["contexts"] = ens["context"].apply(
    lambda lst: [str(x) if x is not None else "" for x in lst]
)  # 리스트 그대로


# Dataset1
ens1 = ens.iloc[0:10, :]

ragas_dataset1 = Dataset.from_pandas(
    ens1[["question", "answer", "ground_truth", "contexts"]]
)
# Dataset2 생성
ragas_dataset100 = Dataset.from_pandas(
    ens[["question", "answer", "ground_truth", "contexts"]]
)

/Users/limseongbeom/anaconda3/envs/voltai/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
# ==============================================================
# 7️⃣ RAGAS 평가 실행
# ==============================================================
result1 = evaluate(
    dataset=ragas_dataset1,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result1)

result100 = evaluate(
    dataset=ragas_dataset100,
    metrics=[context_precision, faithfulness, answer_relevancy, context_recall],
    column_map={
        "user_input": "question",
        "ai_output": "answer",
        "reference": "ground_truth",
        "retrieved_contexts": "contexts",
        "response": "answer",
    },
)

print(result100)

Evaluating: 100%|██████████| 40/40 [01:04<00:00,  1.61s/it]


{'context_precision': 0.9257, 'faithfulness': 0.1401, 'answer_relevancy': 0.7870, 'context_recall': 0.6822}


Evaluating: 100%|██████████| 400/400 [08:08<00:00,  1.22s/it]


{'context_precision': 0.9128, 'faithfulness': 0.2143, 'answer_relevancy': 0.7767, 'context_recall': 0.6738}


In [ ]:
mul_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/multiagent_cat3_context_df.csv"
)
mul = pd.read_csv(mul_path)

In [ ]:
mul

paper_num                                        json_answer  \
0          56  {'Morphological Properties': {'Particle size':...   
1          44  {'Morphological Properties': {'ParticleSize': ...   
2          42  {'Morphological Properties': {'Particle size':...   
3          41  {'Morphological Properties': {'Particle size':...   
4          40  {'Morphological Properties': {'Particle size':...   
..        ...                                                ...   
95         39  {'Morphological Properties': {'ParticleSize': ...   
96         35  {'Morphological Properties': {'Particle size':...   
97         22  {'Morphological Properties': {'ParticleSize': ...   
98         16  {'Morphological Properties': {'ParticleSize': ...   
99         11  {'Morphological Properties': {'ParticleSize': ...   

                                            context_0  \
0   For confirming the microstructural information...   
1   Electrode Preparation and Battery Assembly. Th...   
2   3. Results and discussion\n\nFig. 2 shows the ...   
3   The SEM images for the pristine NCM-811, g-C3N...   
4   each\n\nonly\n\ncase\n\nand\n\nthe\n\nthe\n\nI...   
..                                                ...   
95  2205122  (3 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
96  4. Conclusions\n\nand\n\ncurrent\n\n(GITT),\n\...   
97  Results and Discussion\nThe XRD patterns of pr...   
98  Figure 2 shows the SEM and TEM images of NCM a...   
99  6\n\nA. Habibi et al. / Journal of Alloys and ...   

                                            context_1  \
0   15247\n\nF I G U R E 2\nimage on the cross-sec...   
1   ACS Omega\n\nArticle\n\npolymer/γ-Al2O3-coated...   
2   In order to cope with the above problems, scho...   
3   ACS Omega\n\nhttp://pubs.acs.org/journal/acsod...   
4   3.3% may be close to the optimum value achieva...   
..                                                ...   
95  3. Conclusions\n\nHerein, it is unequivocally ...   
96  The studies of the LiNi0.85Co0.10Mn0.05O2 elec...   
97  XPS analysis was performed to gain further inf...   
98  was conducted on the electrochemical equipment...   
99  Different fractions of RGO (1, 3 and 5 wt %) w...   

                                            context_2  \
0   DLiþ 1⁄4 R2T2=2n4F4A2σ2c2\n\nZ0 1⁄4 Rct þ Re þ...   
1   site\n\n3a\n\n3b\n\n6c\n\nx\n\n0\n0\n0\n0\n0\n...   
2   NJC\n\nPAPER\n\nCite this: New J. Chem., 2021,...   
3   via centrifugation at a speed of 5000 rpm for ...   
4   juergen.janek@phys.chemie.\n\nIncreasing the N...   
..                                                ...   
95  Small 2023, 19, 2205122\n\n2205122  (6 of 13)\...   
96  A.V. Ivanishchev et al.\n\nJournal of Electroa...   
97  experimental section\nFor  the  synthesis  of ...   
98  ACS Applied Materials & Interfaces\n\nResearch...   
99  The electrochemical performances of the as-pre...   

                                            context_3  \
0   3\n\n| R E S U L T A N D DI S C U S S I O N\n\...   
1   Figure 1a. NCM622 particles were first soaked ...   
2   2.3 Electrochemical measurement\n\nCR2032 butt...   
3   Downloaded via CHUNG-ANG UNIV on December 27, ...   
4   Journal of The Electrochemical Society, 2022 1...   
..                                                ...   
95  2205122  (2 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
96  A.V. Ivanishchev et al.\n\nJournal of Electroa...   
97  4\n\nwww.nature.com/scientificreportswww.natur...   
98  The Nyquist plots are fitted and presented in ...   
99  As mentioned above, the RGO was added to the N...   

                                            context_4  \
0   2\n\n| EXPERIMENTAL\n\nand\n\n2.24786 g)\n\nth...   
1   This is an open access article published under...   
2   2. Experimental section\n2.1 Synthesis of the ...   
3   for\n\nThe electrochemical performance is furt...   
4   Supplementary material for this article is ava...   
..                                                ...   
95  investigated  using  XRD  analysis,  and \n\

In [8]:
mapping = dict(zip(df_out['Paper ID'], df_out['Properties']))
ens['output_discussion'] = ens['paper_num'].map(mapping)

In [9]:
json_paths = [
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_011_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_016_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_022_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_035_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_039_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_040_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_041_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_042_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_044_gt.json",
    "/Users/limseongbeom/Desktop/Code/VOLTAI/data/ground_truth/paper_056_gt.json",
]

mul_path = (
    "/Users/limseongbeom/Desktop/Code/VOLTAI/evaluation/multiagent_cat3_context_df.csv"
)
mul = pd.read_csv(mul_path)

# ground_truth 딕셔너리 생성
gt_dict = {}
for path in json_paths:
    paper_num = path.split("/")[-1].split("_")[1]  # 파일명에서 paper_num 추출
    with open(path, "r", encoding="utf-8") as f:
        data = json.load(f)
    gt_dict[paper_num] = data["Morphological Properties"]

# paper_num을 3자리 문자열로 변환하여 매핑
mul["paper_num_str"] = mul["paper_num"].apply(lambda x: f"{x:03d}")
mul["ground_truth"] = mul["paper_num_str"].map(gt_dict)
mul["ground_truth"] = mul["ground_truth"].apply(
    lambda x: x if isinstance(x, dict) else {}
)

# ==============================================================
# 3️⃣ Context 통합
# ==============================================================
context_cols = [f"context_{i}" for i in range(9)]
mul["context"] = mul[context_cols].values.tolist()  # 리스트 형태로 합치기

mul.drop("paper_num_str", axis=1, inplace=True)

# ==============================================================
# 4️⃣ Question 정의
# ==============================================================
question_template =     """question_text: |
    Fill out in the `null`, `[]` and `{}` values based on the example format:

template: 
    Morphological Properties:
        Particle size: {}
        Particle shape: {}
        Particle distribution: {}
        Coating layer characteristics: {}
        Crystal structure and lattice characteristics: {}
"""

mul["question_list"] = [question_template] * len(mul)

# ==============================================================
# 5️⃣ 문자열 변환: RAGAS에서 Arrow 호환되도록
# ==============================================================
mul["answer_str"] = mul["json_answer"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)
mul["ground_truth_str"] = mul["ground_truth"].apply(
    lambda x: json.dumps(x) if isinstance(x, dict) else str(x)
)

# ==============================================================
# 6️⃣ 열 이름 통일 및 Dataset 생성
# ==============================================================
mul["question"] = mul["question_list"]  # 문자열
mul["answer"] = mul["answer_str"]  # 문자열
mul["ground_truth"] = mul["ground_truth_str"]  # 문자열
mul["contexts"] = mul["context"].apply(
    lambda lst: [str(x) if x is not None else "" for x in lst]
)  # 리스트 그대로

mul = mul.iloc[10:20, :]
# # Dataset1
# ens1 = ens.iloc[0:10, :]

# ragas_dataset1 = Dataset.from_pandas(
#     ens1[["question", "answer", "ground_truth", "contexts"]]
# )
# # Dataset2 생성
# ragas_dataset100 = Dataset.from_pandas(
#     ens[["question", "answer", "ground_truth", "contexts"]]
# )

In [10]:
mul

paper_num                                        json_answer  \
10         11  {'Morphological Properties': {'ParticleSize': ...   
11         16  {'Morphological Properties': {'Particle size':...   
12         22  {'Morphological Properties': {'Particle size':...   
13         35  {'Morphological Properties': {'ParticleSize': ...   
14         39  {'Morphological Properties': {'Particle size':...   
15         40  {'Morphological Properties': {'ParticleSize': ...   
16         41  {'Morphological Properties': {'Particle size':...   
17         42  {'Morphological Properties': {'ParticleSize': ...   
18         44  {'Morphological Properties': {'Particle size':...   
19         56  {'Morphological Properties': {'ParticleSize': ...   

                                            context_0  \
10  6\n\nA. Habibi et al. / Journal of Alloys and ...   
11  Figure 2 shows the SEM and TEM images of NCM a...   
12  Results and Discussion\nThe XRD patterns of pr...   
13  4. Conclusions\n\nand\n\ncurrent\n\n(GITT),\n\...   
14  2205122  (3 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
15  each\n\nonly\n\ncase\n\nand\n\nthe\n\nthe\n\nI...   
16  The SEM images for the pristine NCM-811, g-C3N...   
17  3. Results and discussion\n\nFig. 2 shows the ...   
18  ACS Omega\n\nArticle\n\npolymer/γ-Al2O3-coated...   
19  For confirming the microstructural information...   

                                            context_1  \
10  Different fractions of RGO (1, 3 and 5 wt %) w...   
11  was conducted on the electrochemical equipment...   
12  XPS analysis was performed to gain further inf...   
13  The studies of the LiNi0.85Co0.10Mn0.05O2 elec...   
14  3. Conclusions\n\nHerein, it is unequivocally ...   
15  3.3% may be close to the optimum value achieva...   
16  ACS Omega\n\nhttp://pubs.acs.org/journal/acsod...   
17  In order to cope with the above problems, scho...   
18  Figure 1a. NCM622 particles were first soaked ...   
19  15247\n\nF I G U R E 2\nimage on the cross-sec...   

                                            context_2  \
10  The electrochemical performances of the as-pre...   
11  ACS Applied Materials & Interfaces\n\nResearch...   
12  experimental section\nFor  the  synthesis  of ...   
13  A.V. Ivanishchev et al.\n\nJournal of Electroa...   
14  investigated  using  XRD  analysis,  and \n\nB...   
15  juergen.janek@phys.chemie.\n\nIncreasing the N...   
16  via centrifugation at a speed of 5000 rpm for ...   
17  NJC\n\nPAPER\n\nCite this: New J. Chem., 2021,...   
18  site\n\n3a\n\n3b\n\n6c\n\nx\n\n0\n0\n0\n0\n0\n...   
19  DLiþ 1⁄4 R2T2=2n4F4A2σ2c2\n\nZ0 1⁄4 Rct þ Re þ...   

                                            context_3  \
10  As mentioned above, the RGO was added to the N...   
11  Table 4. EIS Parameters of NCM and NCM/C after...   
12  4\n\nwww.nature.com/scientificreportswww.natur...   
13  A.V. Ivanishchev et al.\n\nJournal of Electroa...   
14  2205122  (2 of 13)\n\n© 2022 Wiley-VCH GmbH\n\...   
15  Journal of The Electrochemical Society, 2022 1...   
16  for\n\nThe electrochemical performance is furt...   
17  2.3 Electrochemical measurement\n\nCR2032 butt...   
18  Electrode Preparation and Battery Assembly. Th...   
19  3\n\n| R E S U L T A N D DI S C U S S I O N\n\...   

                                            context_4  \
10  (cid:3)12 cm2 s\n\n4. Conclusion\n\nSolution c...   
11  The Nyquist plots are fitted and presented in ...   
12  V-0.02\n\nRSEI(Ω)\n\n35.838\n\n20.826\n\n26.66...   
13  Journal of Electroanalytical Chemistry 932 (20...   
14  Small 2023, 19, 2205122\n\n2205122  (6 of 13)\...   
15  Supplementary material for this article is ava...   
16  configurations in the dQ/dV curve. While for t...   
17  2. Experimental section\n2.1 Synthesis of the ...   
18  This is an open access article published under...   
19  2\n\n| EXPERIMENTAL\n\nand\n\n2.24786 g)\n\nth...   

                                            context_5  \
10  The graphene-based materials synthesized by th...   
1